## This notebook provides some simple illustrations to the course Many-body physics and quantum computation, delivered by Kareljan Schoutens at the GGI SFT 2022 PhD School, February 2022

### Goal: illustration of Quantum Phase Estimation for 2-site Hubbard model


In [1]:
import cirq
import numpy as np
import matplotlib.pyplot as plt

from IPython.core.display import HTML
display(HTML("<style>pre { white-space: pre !important; }</style>"))

In [2]:
# Get qubits for the phase estimation circuit.

n_bits=2

qubits = cirq.LineQubit.range(n_bits)

u_bit = cirq.NamedQubit('u')

q0=cirq.NamedQubit('u0')
q1=cirq.NamedQubit('u1')

In [3]:
def make_qft_inverse(qubits):
    """Generator for the inverse QFT on a list of qubits."""
    qreg = list(qubits)[::-1]
    while len(qreg) > 0:
        q_head = qreg.pop(0)
        yield cirq.H(q_head)
        for i, qubit in enumerate(qreg):
            yield (cirq.CZ ** (-1 / 2 ** (i + 1)))(qubit, q_head)
        

### example with U=Z**(2*theta)

In [4]:
"""Set up the unitary and number of bits to use in phase estimation."""
# Value of θ which appears in the definition of the unitary U above.
# Try different values.
theta = 1/2+1/8+1/32+1/64
print("theta =",theta)

# Define the unitary U.
U = cirq.Z ** (2 * theta)

Utheta=cirq.Z ** (theta)
Uminustheta=cirq.Z ** (-theta)

# Accuracy of the estimate for theta. Try different values.
n_bits = 6

theta = 0.671875


In [5]:
"""Build the first part of the circuit for phase estimation."""
# Get qubits for the phase estimation circuit.
qubits = cirq.LineQubit.range(n_bits)
u_bit = cirq.NamedQubit('u')

# Build the first part of the phase estimation circuit.
phase_estimator = cirq.Circuit(cirq.H.on_each(*qubits))

for i, bit in enumerate(qubits):
    phase_estimator.append(cirq.ControlledGate(U).on(bit, u_bit) ** (2 ** (n_bits - i - 1)))

print(phase_estimator)

0: ───H───@─────────────────────────────────────────────────────
          │
1: ───H───┼───@─────────────────────────────────────────────────
          │   │
2: ───H───┼───┼──────@──────────────────────────────────────────
          │   │      │
3: ───H───┼───┼──────┼────────@─────────────────────────────────
          │   │      │        │
4: ───H───┼───┼──────┼────────┼──────────@──────────────────────
          │   │      │        │          │
5: ───H───┼───┼──────┼────────┼──────────┼───────────@──────────
          │   │      │        │          │           │
u: ───────Z───S^-1───Z^0.75───Z^(-5/8)───Z^(11/16)───Z^-0.656───


Below an equivalent circuit with the controled rotation gates compiled into CNOT and 1-qubit gates

In [6]:
"""Build the first part of the circuit for phase estimation."""
# Get qubits for the phase estimation circuit.
qubits = cirq.LineQubit.range(n_bits)
u_bit = cirq.NamedQubit('u')

# Build the first part of the phase estimation circuit.
phase_estimator = cirq.Circuit(cirq.H.on_each(*qubits))

for i, bit in enumerate(qubits):
    phase_estimator.append(Utheta.on(u_bit)** (2 ** (n_bits - i - 1)))
    phase_estimator.append(cirq.CNOT.on(bit,u_bit))
    phase_estimator.append(Uminustheta.on(u_bit)** (2 ** (n_bits - i - 1)))
    phase_estimator.append(cirq.CNOT.on(bit,u_bit))
    phase_estimator.append(Utheta.on(bit)** (2 ** (n_bits - i - 1)))

print(phase_estimator)

0: ───H──────@───────@───S^-1───────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
             │       │
1: ───H──────┼───────┼────────────@─────────────@───Z^0.75──────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
             │       │            │             │
2: ───H──────┼───────┼────────────┼─────────────┼──────────────@─────────────@───Z^(-5/8)───────────────────────────────────────────────────────────────────────────────────────────────
             │       │            │             │              │             │
3: ───H──────┼───────┼────────────┼─────────────┼──────────────┼─────────────┼───────────────@────────────────@───Z^(11/16)─────────────────────────────────────────────────────────────
             │       │            │             │              │             │               │              

In [7]:
"""Build the last part of the circuit (inverse QFT) for phase estimation."""
# Do the inverse QFT.
phase_estimator.append(make_qft_inverse(qubits[::-1]))

# Add measurements to the end of the circuit
phase_estimator.append(cirq.measure(*qubits, key='m'))
print(phase_estimator)

                                                                                                                                                                                                                             ┌─────────┐
0: ───H──────@───────@───S^-1─────H────────────────────────────@──────────────────────────────────@──────────────────────────────────────@────────────────────────────────────────@───────────────────────────────────────────@──────────────────────────────────────────────────────────M('m')───
             │       │                                         │                                  │                                      │                                        │                                           │                                                          │
1: ───H──────┼───────┼────────────@─────────────@───Z^0.75─────@^-0.5───H─────────────────────────┼─────────@────────────────────────────┼──────────@─────────────────────────────┼───────────@──

In [8]:
"""Set the input state of the eigenvalue register."""
# Add gate to change initial state
phase_estimator.insert(0, cirq.X(u_bit))

print(phase_estimator)

                                                                                                                                                                                                                                 ┌─────────┐
0: ───────H──────@───────@───S^-1─────H────────────────────────────@──────────────────────────────────@──────────────────────────────────────@────────────────────────────────────────@───────────────────────────────────────────@──────────────────────────────────────────────────────────M('m')───
                 │       │                                         │                                  │                                      │                                        │                                           │                                                          │
1: ───────H──────┼───────┼────────────@─────────────@───Z^0.75─────@^-0.5───H─────────────────────────┼─────────@────────────────────────────┼──────────@────────────────────────────

In [9]:
"""Simulate the circuit and convert from measured bit values to estimated θ values."""
# Simulate the circuit.
sim = cirq.Simulator()
result = sim.run(phase_estimator, repetitions=10)
print(result)
# Convert from output bitstrings to estimate θ values.
theta_estimates = np.sum(2 ** np.arange(n_bits) * result.measurements['m'], axis=1) / 2**n_bits
print(theta_estimates)

m=1111111111, 1111111111, 0000000000, 1111111111, 0000000000, 1111111111
[0.671875 0.671875 0.671875 0.671875 0.671875 0.671875 0.671875 0.671875
 0.671875 0.671875]


### example with U=Exp[i a Hhub] on 2 qubits q0, q1

In [11]:
"""Define the Hubbard gate on two qubits."""

def UHub(alpha,u,t):

    sr=np.sqrt(16*t**2+u**2)

    M0=np.array([[1,0,0,0],[0,1,0,0],[0,0,1,0],[0,0,0,1]])
    M1=np.array([[1,0,0,0],[0,1,0,0],[0,0,-1,0],[0,0,0,-1]])
    M2=np.array([[0,0,1,1],[0,0,1,1],[1,1,0,0],[1,1,0,0]])
    M3=np.array([[1,1,0,0],[1,1,0,0],[0,0,1,1],[0,0,1,1]])
    M4=np.array([[1,1,0,0],[1,1,0,0],[0,0,-1,-1],[0,0,-1,-1]])
    
    U0=np.cos(alpha*u/2)*M0
    U1= -1.0j*np.sin(alpha*u/2)*M1
    U2= -1.0j*(2*t/sr)*np.sin(alpha*sr/2)*M2
    U3=(-np.cos(alpha*u/2)+np.cos(alpha*sr/2))/2*M3
    U4= (-1.0j*u/(2*sr)*np.sin(alpha*sr/2)+(1.0j/2)*np.sin(alpha*u/2))*M4

    UHub=U0+U1+U2+U3+U4
    
    return UHub 

Check unitarity of UHub

In [12]:
myU=UHub(0.1,3,1)
myU_dag=np.conj(myU.T)
# print(np.around(myU,3))
# print()
# print(np.around(myU_dag,3))
# print()
print("display the product of U U_dag to check unitarity")
print()
print(np.around(np.dot(myU,myU_dag),4))


display the product of U U_dag to check unitarity

[[ 1.+0.j -0.-0.j  0.+0.j  0.+0.j]
 [-0.+0.j  1.+0.j -0.+0.j -0.+0.j]
 [ 0.+0.j -0.+0.j  1.+0.j -0.+0.j]
 [ 0.+0.j -0.+0.j -0.-0.j  1.+0.j]]


In [13]:
class HubbardGate(cirq.Gate):
    def __init__(self,alpha,u,t):
        super(HubbardGate, self)
        self.alpha=alpha
        self.u=u
        self.t=t
    
    def _num_qubits_(self):
        return 2

    def _unitary_(self):
        return UHub(self.alpha,self.u,self.t)
    
    def _circuit_diagram_info_(self, args):
        return f"UHub({np.around(self.alpha,2),self.u,self.t})", f"UHub({np.around(self.alpha,2),self.u,self.t})"
    
def Hubbard_layer(alpha,u,t,bit):
    yield HubbardGate(alpha,u,t).on(q0,q1).controlled_by(qubits[bit])

### Choosing U=3/8, t=1/8

reference: eigenvalues for this choice of $U$, $t$ are

GS energy $-5/16$, modulo 1 this becomes 11/16=.6857

1st excited energy $-3/16$, modulo 1 this becomes 13/16=.8125

2nd excited energy $3/16$, modulo 1 this becomes 3/16=.1875

3rd excited energy $5/16$, modulo 1 this becomes 5/16=.3125

In [14]:
"""Build the first part of the circuit for phase estimation."""

n_bits = 4

# Get qubits for the phase estimation circuit.
qubits = cirq.LineQubit.range(n_bits)

# Build the first part of the phase estimation circuit.
phase_estimator = cirq.Circuit(cirq.H.on_each(*qubits))

#phase_estimator.append(Heis_layer(np.pi/5,1))

for i, bit in enumerate(qubits):
    phase_estimator.append(Hubbard_layer((2**i)*2*np.pi,3/8,1/8,n_bits-1-i))

print(phase_estimator)

0: ────H────────────────────────────────────────────────────────────────────────────────────────────@─────────────────────────────
                                                                                                    │
1: ────H──────────────────────────────────────────────────────────────@─────────────────────────────┼─────────────────────────────
                                                                      │                             │
2: ────H────────────────────────────────@─────────────────────────────┼─────────────────────────────┼─────────────────────────────
                                        │                             │                             │
3: ────H───@────────────────────────────┼─────────────────────────────┼─────────────────────────────┼─────────────────────────────
           │                            │                             │                             │
u0: ───────UHub((6.28, 0.375, 0.125))───UHub((12.57, 0.375, 0.125))─

In [15]:
"""Build the last part of the circuit (inverse QFT) for phase estimation."""
# Do the inverse QFT.
phase_estimator.append(make_qft_inverse(qubits[::-1]))

# Add measurements to the end of the circuit
phase_estimator.append(cirq.measure(*qubits, key='m'))
print(phase_estimator)

                                                                                                                                               ┌────────┐   ┌──────────────┐   ┌────────┐
0: ────H────────────────────────────────────────────────────────────────────────────────────────────@─────────────────────────────H───@─────────@────────────@───────────────────────────────────────────M('m')───
                                                                                                    │                                 │         │            │                                           │
1: ────H──────────────────────────────────────────────────────────────@─────────────────────────────┼─────────────────────────────────@^-0.5────┼──────H─────┼───────@──────────@────────────────────────M────────
                                                                      │                             │                                           │            │       │          │            

Initial state: putting Hadamard on q1 produces initial Hubbard model state ${1 \over \sqrt{2}}(|00\rangle+|01\rangle)$ 
with substantial overlap with GS for $U>0$. 

In [16]:
"""Set the input state of the eigenvalue register."""
# Add gate to change initial state

phase_estimator.insert(0, cirq.H(q1))

print(phase_estimator)

                                                                                                                                               ┌────────┐   ┌──────────────┐   ┌────────┐
0: ────H────────────────────────────────────────────────────────────────────────────────────────────@─────────────────────────────H───@─────────@────────────@───────────────────────────────────────────M('m')───
                                                                                                    │                                 │         │            │                                           │
1: ────H──────────────────────────────────────────────────────────────@─────────────────────────────┼─────────────────────────────────@^-0.5────┼──────H─────┼───────@──────────@────────────────────────M────────
                                                                      │                             │                                           │            │       │          │            

In [17]:
"""Simulate the circuit and convert from measured bit values to estimated θ values."""
# Simulate the circuit.
sim = cirq.Simulator()
result = sim.run(phase_estimator, repetitions=20)
print(result)
# Convert from output bitstrings to estimate θ values.
theta_estimates = np.sum(2 ** np.arange(n_bits) * result.measurements['m'], axis=1) / 2**n_bits
print(theta_estimates)

m=11111111111111111111, 11111111111110111111, 00000000000001000000, 11111111111110111111
[0.6875 0.6875 0.6875 0.6875 0.6875 0.6875 0.6875 0.6875 0.6875 0.6875
 0.6875 0.6875 0.6875 0.3125 0.6875 0.6875 0.6875 0.6875 0.6875 0.6875]


Indeed, the measured values for the phase correspond predominantly to 0.6875, 
corresponding to the GS energy $-5/16$ (the probability for hitting this value is 4/5).

Putting an additional X gate on qubit q0 gives initial state 
${1 \over \sqrt{2}}(|10\rangle+|11\rangle)$ 
with much smaller overlap with GS for $U>0$. 

In [18]:
"""Set the input state of the eigenvalue register."""
# Add gate to change initial state

phase_estimator.insert(0, cirq.X(q0))

print(phase_estimator)

                                                                                                                                               ┌────────┐   ┌──────────────┐   ┌────────┐
0: ────H────────────────────────────────────────────────────────────────────────────────────────────@─────────────────────────────H───@─────────@────────────@───────────────────────────────────────────M('m')───
                                                                                                    │                                 │         │            │                                           │
1: ────H──────────────────────────────────────────────────────────────@─────────────────────────────┼─────────────────────────────────@^-0.5────┼──────H─────┼───────@──────────@────────────────────────M────────
                                                                      │                             │                                           │            │       │          │            

In [19]:
"""Simulate the circuit and convert from measured bit values to estimated θ values."""
# Simulate the circuit.
sim = cirq.Simulator()
result = sim.run(phase_estimator, repetitions=20)
print(result)
# Convert from output bitstrings to estimate θ values.
theta_estimates = np.sum(2 ** np.arange(n_bits) * result.measurements['m'], axis=1) / 2**n_bits
print(theta_estimates)

m=11111111111111111111, 01101000001100000000, 10010111110011111111, 01101000001100000000
[0.3125 0.6875 0.6875 0.3125 0.6875 0.3125 0.3125 0.3125 0.3125 0.3125
 0.6875 0.6875 0.3125 0.3125 0.3125 0.3125 0.3125 0.3125 0.3125 0.3125]


Indeed, now the measured values for the phase correspond predominantly to 0.3125, 
corresponding to energy $5/16$ (the probability for hitting this value is again 4/5).